---

# S06E02 : Concurrency - The threading module

Cyril Desjouy

--- 

## 1. Introduction

Comme nous l'avons vu en introduction de cette série de notebooks, un ***thread*** est un fil d'exécution séparé. Sous Python, les *threads* ne s'exécutent pas en parallèle à cause du ***GIL***. De ce fait, l'utilisation de *threads* ne permet pas *nécessairement* de faire tourner un programme plus vite (cela dépend du type de tâche), mais plutôt de structurer de manière plus claire les applications. Les *threads* sont classiquement utilisés pour:

* la création d'application graphiques réactives,
* l'optimisation des communications avec les périphériques (réseau, stockage, ...).

Sous Python, le module `threading` fourni dans la bibliothèque standard propose les outils classiques pour manipuler les *threads* à savoir:

* La classe `Thread` (analogue à la classe `Process` de `multiprocessing`) permettant d'instancier des *threads*.
* La classe `Timer` permettant de créer un *thread* dont l'exécution est différée.
* Toutes les primitives de synchronisation de *threads* que nous étudierons dans un prochain notebook.


**Note:** *Il existe de grandes similitudes entre ce notebook et le précédent portant sur le module `multiprocessing`. Les classes `multiprocessing.Process` et `threading.Thread` sont effectivement très similaires comme vous pourrez le voir.*

## 2. La classe `Thread`


Le coeur du module `threading` est la classe `Thread`. Cette classe permet  de créer des ***threads*** de deux manières différentes:

* en passant un objet ***callable*** en tant qu'argument d'entrée au constructeur,
* en remplaçant la méhode `run()` dans une sous-classe de `Thread` (et uniquement cette méthode).

### 2.1. Avec un ***callable***

Pour démarrer un ***thread***, il suffit de créer une instance de `Thread` initialisée avec un objet ***callable*** puis d'utiliser la méthode `start()` héritée par l'instance. La syntaxe est la suivante:
```python
Thread(target=None, name=None, args=(), kwargs={}, *, daemon=None)
```
où:
* `target`: ***callable***,
* `args` et `kwargs`: arguments à passer au ***callable***,
* `name`: le nom du ***thread***,
* `daemon`: le ***thread*** doit il être lancé en tant que ***daemon***.

***Note:*** *Un programme ne s'arrête que lorsque tous les ***threads*** lancés par ce programme sont terminés. Un **daemon** est un **thread** qui sera tué automatiquement, peu importe son état, lorsque le programme s'arrêtera.*

Dans l'exemple suivant, l'objet ***callable*** est ici la fonction `avenger`. 

<div class="alert alert-block alert-info">
Exécuter cet exemple plusieurs fois et observez attentivement la sortie standard. Essayez à nouveau avec la ligne 6 commentée (le premier <code>sleep</code>).
</div>

In [3]:
import threading
import sys, time, random

def avenger(name):
    current = threading.currentThread().getName()
    time.sleep(random.random())
    sys.stdout.write(f'{current}: {name} comes to save the world!\n')
    time.sleep(random.random())
    sys.stdout.write(f'{current}: {name} finished his work.\n')

if __name__ == '__main__':
    
    current = threading.currentThread().getName()
    thread1 = threading.Thread(target=avenger, args=('Ironman',))
    thread2 = threading.Thread(target=avenger, args=('Captain',))

    sys.stdout.write(f'{current}: Calling Ironman.\n')
    thread1.start()                     # Start thead1
    sys.stdout.write(f'{current}: Calling Captain.\n')
    thread2.start()                     # Start thead2
    
    sys.stdout.write(f'{current}: Waiting Ironman & Captain for saving the world!\n')
    thread1.join()                      # wait for thread1 to finish
    thread2.join()                      # wait for thread2 to finish
    sys.stdout.write(f'{current}: Oh yeah! They saved us!\n')

MainThread: Calling Ironman.
MainThread: Calling Captain.
MainThread: Waiting Ironman & Captain for saving the world!
Thread-8: Captain comes to save the world!
Thread-8: Captain finished his work.
Thread-7: Ironman comes to save the world!
Thread-7: Ironman finished his work.
MainThread: Oh yeah! They saved us!


Les instances de `Thread` sont créées lignes 14-15 avec l'objet ***callable*** `avenger` prenant pour arguments `args`. Les deux instances sont ensuite démarrées à l'aide de la méthode `start()`. La méthode `join()` signifie à l'interpréteur qu'il doit attendre que `thread1` et `thread2` soient terminés avant de passer aux instructions suivantes du programme principal. Cette fonction est bloquante. Elle ne retourne (`None`) que lorsque le thread a effectivement fini son exécution. 

<div class="alert alert-block alert-info">
Sur l'exemple précédent, essayez de commenter les lignes 23-24 (les deux <code>join()</code>) et observez la différence.
</div>

Lorsqu'il est nécesaire de lancer de nombreux ***threads***, il peut être plus pratique d'automatiser ceci en utilisant des boucles comme le montre l'exemple suivant:

In [4]:
import threading
import sys, time, random

def avenger(name):
    current = threading.currentThread().getName()
    time.sleep(random.random())
    sys.stdout.write(f'{current}: {name} comes to save the world!\n')
    time.sleep(random.random())
    sys.stdout.write(f'{current}: {name} finished his work.\n')

if __name__ == '__main__':
    
    threads = []
    
    for name in ['Ironman', 'Hulk', 'Thor', 'Ant-man', 'Wasp']:
        threads.append(threading.Thread(target=avenger, args=(name,)))
        threads[-1].start()
        
    for thead in threads:
        thread.join()

### 2.2. En subclassant `Thread`

Il est également possible de créer un ***thread*** en subclassant `Thread` et en remplaçant la méthode `run()`:

In [1]:
import threading
import sys, time, random

class Avenger(threading.Thread):
    
    def __init__(self, name):
        super().__init__()           # super is mandatory!
        self.name = name
        
    def run(self):
        current = threading.currentThread().getName()
        time.sleep(random.random())
        sys.stdout.write(f'{current}: {self.name} comes to save the world!\n')
        time.sleep(random.random())
        sys.stdout.write(f'{current}: {self.name} finished his work.\n')

if __name__ == '__main__':
    
    ironman = Avenger('Ironman')
    captain = Avenger('Captain')
    
    ironman.start()
    captain.start()
    
    ironman.join()
    captain.join()

Ironman: Ironman comes to save the world!
Captain: Captain comes to save the world!
Ironman: Ironman finished his work.
Captain: Captain finished his work.


La création et le lancement des ***threads*** suit la même logique que dans les exemples précédents. La seule subtilité ici réside dans le remplacement de la méthode `__init__` de la superclasse `Thread`. Afin de préserver l'initialisation de notre ***thread***, il faudra impérativement appeler la méthode `__init__` de la superclasse à l'aide de `super`.

## 3. La classe `Timer`

La classe `Timer` est une sous classe de `Thread` et fonctionne donc de la même manière. Elle hérite (entre autres) de la méthode `start()` qui permet de lancer l'exécution d'un ***thread*** après un temps spécifié par l'utilisateur. La syntaxe de `Timer` est la suivante:
```
Timer(interval, target, args=None, kwargs=None)
```
L'argument obligatoire `interval` est l'intervale de temps (en sec) avant de démarrer l'exécution du 
***thread***. Il est possible d'arrêter un `Timer` actif avant qu'il soit exécuté à l'aide de la méthode `cancel()`. Si un `Timer` est arrêté de cette manière, il ne se lancera pas, ni ne lèvera d'exception.

Un exemple de `Timer` est présenté ci-dessous:

In [7]:
import threading
import sys, time, random

def avenger(name):
    time.sleep(random.random())
    sys.stdout.write(f'Thread: {name} comes to save the world!\n')
    time.sleep(random.random())
    sys.stdout.write(f'Thread: {name} finished his work.\n')

if __name__ == '__main__':
    
    threads = []
    
    for name in ['Ironman', 'Captain']:
        threads.append(threading.Thread(target=avenger, args=(name,)))
        threads[-1].start()
    
    threads.append(threading.Timer(5, avenger, args=('Wonder Woman',)))    # Wait 5sec before starting thread
    threads[-1].start()

    for thread in threads:              
        thread.join()       

Thread: Captain comes to save the world!
Thread: Ironman comes to save the world!
Thread: Ironman finished his work.
Thread: Captain finished his work.
Thread: Wonder Woman comes to save the world!
Thread: Wonder Woman finished his work.


## 4. Les fonctions utilitaires

Le module `threading` défini un certain nombre de fonctions utilitaires pour la gestions des ***threads*** (fils d'exécution). Les plus utiles sont listées ci-dessous.

* `active_count()`: Retourne le nombre de thread vivants.
* `current_thread()`: Retourne l'objet `Thread` courrant.
* `enumerate()`: Retourne une liste de tous les objets `Thread` vivants.
* ...

Notez bien que cette liste est non exhaustive!

<div class="alert alert-block alert-info">
Testez par exemple la méthode <code>enumerate()</code> pour lister les <b>threads</b> vivants. Vous vous apercevrait que certains n'ont pas été crées par vous. C'est en effet Jupyter qui les a lancé à son démarrage.
</div>

In [9]:
threading.enumerate()

[<_MainThread(MainThread, started 139842360768320)>,
 <Thread(Thread-2, started daemon 139842277320448)>,
 <Heartbeat(Thread-3, started daemon 139842268927744)>,
 <HistorySavingThread(IPythonHistorySavingThread, started 139842037995264)>,
 <ParentPollerUnix(Thread-1, started daemon 139842029602560)>]

## Bibliographie

* [python.org - threading](https://docs.python.org/3.8/library/threading.html)

## Application

<div class="alert alert-block alert-info">
Soon.
</div>